# Alternating Algorithm

We want to solve the right definite two-parameter eigenvalue

$$
A_1u+\lambda B_1u+\mu C_1u=0,\\
A_2v+\lambda B_2v+\mu C_2v=0.
$$

First we generate matrices satisfying the assumptions, i.e., the matrices $C_2$ and $C_1\otimes B_2-C_2\otimes B_1$ are positive definite and $C_1$ is negative definite.

In [1]:
using LinearAlgebra

n=30

A1=randn(n,n); A1=A1'+A1
A2=randn(n,n); A2=A2'+A2

S1=randn(n,n);S2=randn(n,n)
B1=S1*Matrix(Diagonal(rand(n).-0.5))*S1'
B2=S2*Matrix(Diagonal(rand(n).-1.5))*S2'
C1=-S1*S1'
C2=S2*S2';

We can run the alternating algorithm for these matrices.

In [2]:
function twopareig_alt(A1,B1,C1,A2,B2,C2,i,j,its)
    #input matrices of the two-parameter eigenvalue problem satisfying the definiteness assumptions and desired index
    #output eigenvalue (lambda,mu) and eigenvector (u,v) of the desired index
    
    #first we need the dimensions of the matrices
    n=size(A1)[1]
    m=size(A2)[1]
    #we can start with a random vector
    u=randn(n)
    v=randn(m)
    lambda=0
    mu=0
    for it in 1:its
        #compute coefficients for the generalized eigenvalue problem
        a=u'*A1*u
        b=u'*B1*u
        c=u'*C1*u

        lhs=a*C2-c*A2
        rhs=c*B2-b*C2

        

        l,V=eigen(lhs,rhs)
        #asking for the sign of c tells us what eigenvalue to look for to get one of the right index
        #if the matrices satsify the assumptions this can be skipped
        if c<0
            v=V[:,j]
            lambda=l[j]
        else
            v=V[:,m+1-j]
            lambda=l[m+1-j]
        end
        
        #we can compute mu here
        mu=-(a+b*lambda)/c

        #the same but for v 
        a=v'*A2*v
        b=v'*B2*v
        c=v'*C2*v

        lhs=c*A1-a*C1
        rhs=b*C1-c*B1

 

        l,U=eigen(lhs,rhs)
        if c>0
            u=U[:,i]
            lambda=l[i]
        else
            u=U[:,n+1-i]
            lambda=l[n+1-i]
        end

        mu=-(a+b*lambda)/c
        
    
        

    end
    return lambda,mu,u,v   
end

twopareig_alt (generic function with 1 method)

We can check this algorithm.

In [3]:
for i in 1:n
    for j in 1:n
        lambda,mu,u,v=twopareig_alt(A1,B1,C1,A2,B2,C2,i,j,5)
        #if the eigenvalue has the right index, then the i-/j-th smallest eigenvalue of A+lambda B+mu C is zero
        test_i=eigvals(A1+lambda*B1+mu*C1)[i]
        test_j=eigvals(A2+lambda*B2+mu*C2)[j]
        if abs(test_i)>1e-9 || abs(test_j)>1e-12
            println("For index ($i,$j)) we have the eigenvalue errors $(test_i) and $(test_j)")
        end
        #We can also check the eigenvectors:
        u/=norm(u)
        v/=norm(v)
        test_i=norm((A1+lambda*B1+mu*C1)*u)
        test_j=norm((A2+lambda*B2+mu*C2)*v)
        if abs(test_i)>1e-9 || abs(test_j)>1e-12
            println("For index ($i,$j)) we have the residual norms $(test_i) and $(test_j)")  
        end
    end
end



For index (1,1)) we have the eigenvalue errors -2.299916338630789e-12 and -1.4848391177983952e-12
For index (1,1)) we have the residual norms 1.007565436068525e-10 and 1.446959527213292e-11
For index (1,2)) we have the residual norms 1.7651240588569298e-12 and 2.768298686231474e-12
For index (1,3)) we have the residual norms 1.4927149015939952e-12 and 2.4495324783729644e-12
For index (1,4)) we have the residual norms 1.450088366871532e-12 and 5.047718549398743e-12
For index (1,5)) we have the residual norms 1.409891692982889e-12 and 3.058063692818418e-12
For index (1,6)) we have the residual norms 1.0930788392527906e-12 and 2.415168623843043e-12
For index (1,7)) we have the residual norms 1.0237747393400498e-12 and 6.358159633868717e-12
For index (1,8)) we have the residual norms 1.013481948562707e-12 and 4.1878980054087244e-12
For index (1,9)) we have the residual norms 1.2543936291098397e-12 and 4.876055458818501e-12
For index (1,10)) we have the residual norms 1.1358851444511637e-12

For index (30,20)) we have the residual norms 4.066721376410742e-12 and 3.539461080983034e-11
For index (30,21)) we have the residual norms 3.891543382300403e-12 and 2.7970121327029345e-11
For index (30,22)) we have the residual norms 3.53811043435239e-12 and 2.570328724182112e-11
For index (30,23)) we have the residual norms 3.5964712099654897e-12 and 1.7869300209728357e-11
For index (30,24)) we have the residual norms 3.772975236270635e-12 and 1.9313645656251936e-11
For index (30,25)) we have the eigenvalue errors -2.4005950489848034e-13 and 1.1056836896375626e-12
For index (30,25)) we have the residual norms 3.725616175432284e-12 and 2.2184011604106884e-11
For index (30,26)) we have the residual norms 3.530811186056904e-12 and 2.645813381337809e-11
For index (30,27)) we have the residual norms 2.4394909677818813e-12 and 2.7717420586929758e-11
For index (30,28)) we have the eigenvalue errors -4.79398514478226e-13 and 1.285041726083163e-12
For index (30,28)) we have the residual norms

These values are all close to machine precision. 

If the matrices do not satisfy these assumptions, we can perform affine transformations to the eigenvalue problem. To test this, let us perform some affine transformation to make $C_1$ and $C_2$ no longer positive definite.

In [4]:
C1=C1+B1; C2=C2+B2;
hcat(eigvals(C1),eigvals(C2))

30×2 Array{Float64,2}:
 -104.634      -25.3977
  -97.3922     -21.675
  -83.1846     -17.2486
  -75.5028     -13.3026
  -63.9637     -11.3747
  -59.8023     -10.3087
  -53.8328      -7.45019
  -51.1422      -6.28786
  -48.6185      -6.09173
  -38.7105      -3.46527
  -33.3855      -2.43435
  -31.1964      -1.86886
  -26.4929      -1.29252
    ⋮          
  -11.5626       0.0436495
   -9.62568      0.159252
   -9.46295      1.12067
   -6.8684       1.27471
   -4.5231       2.56337
   -3.39391      3.68401
   -3.12846      4.59525
   -2.21864      6.62235
   -0.989113     9.05409
   -0.339664    12.058
   -0.0757441   19.1556
   -0.0101906   25.9177

Now $C_2$ might not be definite. The algorithm still works:


In [5]:
for i in 1:n
    for j in 1:n
        lambda,mu,u,v=twopareig_alt(A1,B1,C1,A2,B2,C2,i,j,5)
        #if the eigenvalue has the right index, then the i-/j-th smallest eigenvalue of A+lambda B+mu C is zero
        test_i=eigvals(A1+lambda*B1+mu*C1)[i]
        test_j=eigvals(A2+lambda*B2+mu*C2)[j]
        if abs(test_i)>1e-9 || abs(test_j)>1e-12
            println("For index ($i,$j)) we have the eigenvalue errors $(test_i) and $(test_j)")
        end
        #We can also check the eigenvectors:
        u/=norm(u)
        v/=norm(v)
        test_i=norm((A1+lambda*B1+mu*C1)*u)
        test_j=norm((A2+lambda*B2+mu*C2)*v)
        if abs(test_i)>1e-9 || abs(test_j)>1e-12
            println("For index ($i,$j)) we have the residual norms $(test_i) and $(test_j)")  
        end
    end
end

For index (1,1)) we have the residual norms 3.355453603877696e-10 and 1.1212841657537528e-11
For index (1,2)) we have the residual norms 2.1343458274495683e-12 and 1.4739619919610336e-12
For index (1,3)) we have the residual norms 1.5160589688392827e-12 and 1.9858340727372666e-12
For index (1,4)) we have the residual norms 1.45367893604648e-12 and 1.6618233596782185e-12
For index (1,5)) we have the residual norms 1.475980712854762e-12 and 1.2727668031506047e-12
For index (1,6)) we have the residual norms 1.0144526667852147e-12 and 1.3794460275459853e-12
For index (1,7)) we have the residual norms 1.6304418281178605e-12 and 1.27321452992426e-12
For index (1,10)) we have the residual norms 1.7053158653190288e-12 and 1.1668220674449482e-12
For index (1,13)) we have the residual norms 8.708985730475105e-12 and 5.872939150745087e-12
For index (1,15)) we have the residual norms 1.4929230562633379e-12 and 2.123988650018873e-12
For index (1,16)) we have the residual norms 1.004247141766847e-12

For index (30,19)) we have the residual norms 2.7529198651243984e-12 and 6.549228203095949e-12
For index (30,20)) we have the residual norms 3.940188515456731e-12 and 8.28450367062146e-12
For index (30,21)) we have the residual norms 3.525129909070707e-12 and 6.8402269144736195e-12
For index (30,22)) we have the residual norms 3.599332060020759e-12 and 8.987527338922007e-12
For index (30,23)) we have the residual norms 3.3356349078844303e-12 and 6.8531421104583365e-12
For index (30,24)) we have the residual norms 4.481384641306974e-12 and 7.548479312783976e-12
For index (30,25)) we have the residual norms 3.903732395367044e-12 and 3.611341755224064e-12
For index (30,26)) we have the residual norms 2.0956313370675473e-12 and 6.755710896204468e-12
For index (30,27)) we have the residual norms 3.419578731498809e-12 and 1.2144004777398252e-11
For index (30,28)) we have the residual norms 4.992835717482345e-12 and 5.891036987035551e-12
For index (30,29)) we have the residual norms 3.7686506

We can perform the steps of Remark 2 to get a problem satisfying the definiteness assumptions. In the same steps we can also diagonolize the matrices $B_1,B_2,C_1,C_2$. This requires checking multiple cases.

In [6]:
function affine_transformation_diagonalization(B1,B2,C1,C2)
    #returns diagonal versions of B1,B2,C1,C2 and the corresponding change of basis and affine transformation 
    
    l1,U1=eigen(C1)
    l2,U2=eigen(C2)
    S1=U1;S2=U2
    b1=l1;b2=l2;c1=l1;c2=l2
    #first diagonilize C1 and C2
    #S1,S2 denotes the change of basis
    
    newB1=S1'*B1*S1
    newB2=S2'*B2*S2
    
    #we need to remember the affine transformations
    T=Matrix(Diagonal(ones(2)))
    
    #check definiteness of C2
    if minimum(l2)*maximum(l2)>0
        #C2 is defintite
        if minimum(l1)*maximum(l1)>0

           #C1 is also definite so we only need to diagonalize the B and C matrices
            if l1[1]>0
                S1=S1*Diagonal(sqrt.(l1.^(-1)))
                newB1=Diagonal(sqrt.(l1.^(-1)))*newB1*Diagonal(sqrt.(l1.^(-1)))
                b1,U=eigen(newB1)
                S1=S1*U
                c1.=1
                println(norm(S1'*C1*S1-I))
            else
                S1=S1*Diagonal(sqrt.(-l1.^(-1)))
                newB1=Diagonal(sqrt.(-l1.^(-1)))*newB1*Diagonal(sqrt.(-l1.^(-1)))
                b1,U=eigen(newB1)
                S1=S1*U
                c1.=-1
            end
            if l2[1]>0
                S2=S2*Diagonal(sqrt.(l2.^(-1)))
                newB2=Diagonal(sqrt.(l2.^(-1)))*newB2*Diagonal(sqrt.(l2.^(-1)))
                b2,U=eigen(newB2)
                S2=S2*U
                c2.=1
            else
                S2=S2*Diagonal(sqrt.(-l2.^(-1)))
                newB2=Diagonal(sqrt.(-l2.^(-1)))*newB2*Diagonal(sqrt.(-l2.^(-1)))
                b2,U=eigen(newB2)
                S2=S2*U
                c2.=-1
            end
        else
            
            #We will proceed similarly to the second part of the remark
            #compute the eigenvalues of the gep   B2 u=lambda C2 u
            if l2[1]>0
                S2=S2*Diagonal(sqrt.(l2.^(-1)))
                newB2=Diagonal(sqrt.(l2.^(-1)))*newB2*Diagonal(sqrt.(l2.^(-1)))
                l2.=1
            else
                S2=S2*Diagonal(sqrt.(-l2.^(-1)))
                newB2=Diagonal(sqrt.(-l2.^(-1)))*newB2*Diagonal(sqrt.(-l2.^(-1)))
                l2.=-1
            end
            l,U=eigen(newB2)
            S2=S2*U
            println(norm(S2'*B2*S2-Diagonal(l)))
            #We know that C1-1/lambda B1 is definite for any eigenvalue lambda of B2 
            #C2-1/lambda B2 is semidefinite for extreme eigenvalues of B2
            c=10
            lambda=l[1]
            l3=eigvals(Diagonal(l1)*(lambda-c)-newB1*l2[1])
            while minimum(l3)*maximum(l3)<0
                c/=2
                l3=eigvals(Diagonal(l1)*(lambda-c)-newB1*l2[1])
            end
            T[2,1]=-l2[1]
            T[2,2]=lambda-c
            #we performed an affine transformation
            b2=l;c2=(lambda-c)*l2-l*l2[1]
            newC1=Diagonal(l1)*(lambda-c)-newB1*l2[1]
            #we only need to diagonalize B1 and C1
            l,U=eigen(newC1)
            S1=S1*U
            newB1=U'*newB1*U
            if l[1]>0
                S1=S1*Diagonal(sqrt.(l.^(-1)))
                newB1=Diagonal(sqrt.(l.^(-1)))*newB1*Diagonal(sqrt.(l.^(-1)))
                l.=1
            else
                S1=S1*Diagonal(sqrt.(-l.^(-1)))
                newB1=Diagonal(sqrt.(-l.^(-1)))*newB1*Diagonal(sqrt.(-l.^(-1)))
                l.=-1
            end
            c1=l
            b1,U=eigen(newB1)
            S1=S1*U
        end
    else
        
        #C2 is indefinite, so we can resume as in the remark
        #first we can perform an affine transformation to make B1 definite
        m=length(l2)
        T[1,2]=-newB2[m,m]/l2[m]
        newB1+=Diagonal(l1)*   T[1,2]
        newB2+=Diagonal(l2)*   T[1,2]
        

        #we next diagonalize B1
        l,U=eigen(newB1)
  
        if l[1]>0
            S1=S1*U*Diagonal(sqrt.(l.^(-1)))
            newC1=Diagonal(sqrt.(l.^(-1)))*U'*Diagonal(l1)*U*Diagonal(sqrt.(l.^(-1)))
            b1.=1
        else
            S1=S1*U*Diagonal(sqrt.(-l.^(-1)))
            newC1=Diagonal(sqrt.(-l.^(-1)))*U'*Diagonal(l1)*U*Diagonal(sqrt.(-l.^(-1)))
            b1.=-1
        end
        
    
        
        #now we diagonalize C1 and perform the necessary affine transformations
        l,U=eigen(newC1)
        S1=S1*U
        
 
        
        lambda=maximum(l)
        c=10
        l3=eigvals(Diagonal(l2)-newB2*(lambda+c)/b1[1])
        while minimum(l3)*maximum(l3)<0
            c/=2
            l3=eigvals(Diagonal(l2)-newB2*(lambda+c)/b1[1])
        end
        T[2,:]+=-(lambda+c)/b1[1]*T[1,:]
        c1=l-b1*(lambda+c)/b1[1]
        
    
        
        
        l,U=eigen(Diagonal(l2)-newB2*(lambda+c)/b1[1])
        S2=S2*U
        newB2=U'*newB2*U
 
        if l[1]<0
            c2.=-1
            S2*=Diagonal(sqrt.(-l.^(-1)))
            newB2=Diagonal(sqrt.(-l.^(-1)))*newB2*Diagonal(sqrt.(-l.^(-1)))
        else
            c2.=1
            S2*=Diagonal(sqrt.(l.^(-1)))
            newB2=Diagonal(sqrt.(l.^(-1)))*newB2*Diagonal(sqrt.(l.^(-1)))
        end
        b2,U=eigen(newB2)
        S2=S2*U
    end
    
    return b1,b2,c1,c2,T,S1,S2
end


affine_transformation_diagonalization (generic function with 1 method)

Since we can diagonalize the matrices $B_1,B_2,C_1,C_2$, we can utilize this in our algorithm:

In [7]:
function twopareig_alt_diag(A1,b1,c1,A2,b2,c2,i,j,its)
    
    #input matrices of the two-parameter eigenvalue problem satisfying the definiteness assumptions and desired index
    #b1,c1,b2,c2 are the entries of the diagonal matrices B_1,C_1,B_2,C_2
    #output eigenvalue (lambda,mu) and eigenvector (u,v) of the desired index
    
    #first we need the dimensions of the matrices
    n=size(A1)[1]
    m=size(A2)[1]
    #we can start with a random vector
    u=randn(n)
    v=randn(m)
    lambda=0
    mu=0
    for it in 1:its
        #compute coefficients for the generalized eigenvalue problem
        a=u'*A1*u
        b=u'*Diagonal(b1)*u
        c=u'*Diagonal(c1)*u

        lhs=a*Diagonal(c2)-c*A2
        rhs=c*b2-b*c2

        
        #rhs is definite
        if minimum(rhs)<0
            rhs=Diagonal(sqrt.(-rhs.^(-1)))
            lhs=-rhs*lhs*rhs
            
        else
            rhs=Diagonal(sqrt.(rhs.^(-1)))
            lhs=rhs*lhs*rhs  
        end
        l,V=eigen(Symmetric(lhs))
        #asking for the sign of c tells us what eigenvalue to look for to get one of the right index
        #if the matrices satsify the assumptions this can be skipped
        if c<0
            v=rhs*V[:,j]
            lambda=l[j]
        else
            v=rhs*V[:,m+1-j]
            lambda=l[m+1-j]
        end
        
        #we can compute mu here
        mu=-(a+b*lambda)/c

        #the same but for v 
        a=v'*A2*v
        b=v'*Diagonal(b2)*v
        c=v'*Diagonal(c2)*v

        lhs=c*A1-a*Diagonal(c1)
        rhs=b*c1-c*b1
     
        
        if minimum(rhs)<0
            rhs=Diagonal(sqrt.(-rhs.^(-1)))
            lhs=-rhs*lhs*rhs
        else
            rhs=Diagonal(sqrt.(rhs.^(-1)))
            lhs=rhs*lhs*rhs
        end
        l,U=eigen(Symmetric(lhs))
        if c>0
            u=rhs*U[:,i]
            lambda=l[i]
        else
            u=rhs*U[:,n+1-i]
            lambda=l[n+1-i]
        end

        mu=-(a+b*lambda)/c
   

    end
    return lambda,mu,u,v   
end

twopareig_alt_diag (generic function with 1 method)

We can now effectively compute all eigenvalues of the two-parameter eigenvalue problem.

In [8]:
function twopareig_alt(A1,B1,C1,A2,B2,C2,its)
    #first we perform affine transformations and diagonalization of the matrices B1,B2,C1,C2
    b1,b2,c1,c2,T,S1,S2=affine_transformation_diagonalization(B1,B2,C1,C2)
    A1new=Symmetric(S1'*A1*S1)
    A2new=Symmetric(S2'*A2*S2)
    n=length(b1)
    m=length(b2)
    lambdas=zeros(n,m)
    mus=zeros(n,m)
    U=zeros(n,m,n)
    V=zeros(n,m,m)
    for i in 1:n
        for j in 1:m
            #compute the eigenvalues of the transformed eigenvalue problem
            lambda,mu,u,v=twopareig_alt_diag(A1new,b1,c1,A2new,b2,c2,i,j,its)
            #lambda,mu,u,v=twopareig_alt(A1new,Matrix(Diagonal(b1)),Matrix(Diagonal(c1)),A2new,Matrix(Diagonal(b2)),Matrix(Diagonal(c2)),i,j,its)
            
            #we can get the eigenvalues and eigenvectors of the original problem easily
            lambdas[i,j]=T[1,1]*lambda+T[2,1]*mu
            mus[i,j]=T[1,2]*lambda+T[2,2]*mu
            U[i,j,:]=S1*u
            V[i,j,:]=S2*v
        end
    end
    lambdas,mus,U,V
end


#we can compare this method to the one without performing affine transformations

function twopareig_alt_compare(A1,B1,C1,A2,B2,C2,its)
    n=size(B1)[1]
    m=size(B2)[1]
    lambdas=zeros(n,m)
    mus=zeros(n,m)
    U=zeros(n,m,n)
    V=zeros(n,m,m)
    for i in 1:n
        for j in 1:m
            #compute the eigenvalues of the transformed eigenvalue problem
            lambdas[i,j],mus[i,j],U[i,j,:],V[i,j,:]=twopareig_alt(A1,B1,C1,A2,B2,C2,i,j,its)
        end
    end
    lambdas,mus,U,V
end

twopareig_alt_compare (generic function with 1 method)

Diagonalizing the matrices $B_1,B_2,C_1,C_2$ can save significant time when computing multiple eigenvalues for larger matrices:

In [9]:

println()
println("Time of algorithm with diagonalization")
@time lambdas,mus,U,V= twopareig_alt(A1,B1,C1,A2,B2,C2,5)

@time lambdas,mus,U,V= twopareig_alt(A1,B1,C1,A2,B2,C2,5)
println()
finalerror=0
finalresnorms=0
for i in 1:n
    for j in 1:n
        lambda=lambdas[i,j]
        mu=mus[i,j]
        test_i=minimum(abs.(eigvals(A1+lambda*B1+mu*C1)))
        test_j=minimum(abs.(eigvals(A2+lambda*B2+mu*C2)))
        if abs(test_i)>1e-9 || abs(test_j)>1e-9
            println("For index ($i,$j)) we have the eigenvalue errors $(test_i) and $(test_j)")
        end
        finalerror+=abs(test_i)+abs(test_j)
        u=U[i,j,:]
        v=V[i,j,:]
        u/=norm(u)
        v/=norm(v)
        test_i=norm((A1+lambda*B1+mu*C1)*u)
        test_j=norm((A2+lambda*B2+mu*C2)*v)
        if abs(test_i)>1e-9 || abs(test_j)>1e-9
            println("For index ($i,$j)) we have the residual norms $(test_i) and $(test_j)")  
        end
        finalresnorms+=abs(test_i)+abs(test_j)
        
    end
end
println()
println("the sum of errors is $finalerror")
println("the sum of residual norms is $finalresnorms")
println()


println("Time of algorithm without diagonalization and affine transformation")
@time lambdas,mus,U,V= twopareig_alt_compare(A1,B1,C1,A2,B2,C2,5)
@time lambdas,mus,U,V= twopareig_alt_compare(A1,B1,C1,A2,B2,C2,5)
println()

finalerror=0
finalresnorms=0
for i in 1:n
    for j in 1:n
        lambda=lambdas[i,j]
        mu=mus[i,j]
        test_i=minimum(abs.(eigvals(A1+lambda*B1+mu*C1)))
        test_j=minimum(abs.(eigvals(A2+lambda*B2+mu*C2)))
        if abs(test_i)>1e-9 || abs(test_j)>1e-9
            println("For index ($i,$j)) we have the eigenvalue compare errors $(test_i) and $(test_j)")
        end
        finalerror+=abs(test_i)+abs(test_j)
        u=U[i,j,:]
        v=V[i,j,:]
        u/=norm(u)
        v/=norm(v)
        test_i=norm((A1+lambda*B1+mu*C1)*u)
        test_j=norm((A2+lambda*B2+mu*C2)*v)
        if abs(test_i)>1e-9 || abs(test_j)>1e-9
            println("For index ($i,$j)) we have the compare residual norms $(test_i) and $(test_j)")  
        end
        finalresnorms+=abs(test_i)+abs(test_j)
        
    end
end
println()

println("the sum of compare errors is $finalerror")
println("the sum of compare residual norms is $finalresnorms")
println()

#we can also compare this with the time we need to solve the assiociated n^2 times n^2 eigenvalue problem

println("Time of computing the associated n^2 times n^2 eigenvalue problem")

@time eigen(kron(A1,C2)-kron(C1,A2),kron(C1,B2)-kron(B1,C2));      
@time eigen(kron(A1,C2)-kron(C1,A2),kron(C1,B2)-kron(B1,C2));  


Time of algorithm with diagonalization
 12.543337 seconds (23.34 M allocations: 1.633 GiB, 5.92% gc time)
  2.683528 seconds (263.29 k allocations: 571.902 MiB, 1.39% gc time)


the sum of errors is 1.1980345955734464e-9
the sum of residual norms is 2.161697666562168e-8

Time of algorithm without diagonalization and affine transformation
  4.252455 seconds (449.04 k allocations: 690.123 MiB, 1.44% gc time)
  3.872379 seconds (393.31 k allocations: 687.333 MiB, 1.48% gc time)

For index (10,27)) we have the compare residual norms 1.1863507944073396e-9 and 9.981404090838363e-12
For index (14,1)) we have the compare residual norms 1.0073722157766232e-9 and 1.02716614281728e-11
For index (17,1)) we have the compare residual norms 1.0755401831257006e-9 and 8.78664527667746e-12
For index (30,1)) we have the compare residual norms 1.1265770822014743e-9 and 4.163646323547098e-11

the sum of compare errors is 8.833694326769068e-10
the sum of compare residual norms is 1.939129171690429e-8

Time

Diagonalizing did not increase the error! But for large $n$ we can save a significant amount of time!